In [8]:
import io
import os
import cv2
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from tqdm import tqdm

In [9]:
path = 'dados/CAPTCHA-10k'
save_path = 'dados/processed'
labels_folder = 'labels10k'
if not os.path.exists(save_path):
    os.makedirs(save_path)
num_chars = 6

In [ ]:
def save_cleaned_image(path, folder, filename, save_path):
    img_path = os.path.join(path, folder, filename)
    img_gray = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)

    if img_gray is None:
        print(f"Erro: Não foi possível carregar a imagem em {img_path}")
        return

    # Remoção de ruído
    denoised_img = cv2.medianBlur(img_gray, 3)

    # Binarização (fundo preto, texto branco)
    threshold_value = 80
    _, binary_cleaned_img = cv2.threshold(denoised_img, threshold_value, 255, cv2.THRESH_BINARY_INV)

    # Erosão leve para tentar separar caracteres colados
    kernel = np.ones((2, 2), np.uint8)  # Teste (2,1) se estiver erodindo demais
    binary_cleaned_img = cv2.erode(binary_cleaned_img, kernel, iterations=1)

    # (Opcional) Dilatação para recuperar espessura das letras
    binary_cleaned_img = cv2.dilate(binary_cleaned_img, kernel, iterations=1)

    # Criar pasta de saída
    output_folder_path = os.path.join(save_path, folder, 'cleanImage')
    os.makedirs(output_folder_path, exist_ok=True)

    # Salvar imagem final
    cleaned_filename = f"{os.path.splitext(filename)[0]}{os.path.splitext(filename)[1]}"
    full_output_path = os.path.join(output_folder_path, cleaned_filename)
    cv2.imwrite(full_output_path, binary_cleaned_img)

In [11]:
for folder in tqdm(os.listdir(path), desc="Processing folders"):
    if os.path.isdir(os.path.join(path, folder)) and folder != labels_folder:
        for filename in tqdm(os.listdir(os.path.join(path, folder)), desc=f"Cleaning {folder}", leave=False):
            if filename.endswith('.jpg'):
                save_cleaned_image(path, folder, filename, save_path)


Processing folders: 100%|██████████| 4/4 [00:03<00:00,  1.17it/s]


In [12]:
def split_image(path, folder, filename, save_path,
                        margin=12, max_char_width=48, min_advance=8, debug=False):
    img_path = os.path.join(path, folder, filename)
    img = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)

    if img is None:
        print(f"Erro: Não foi possível carregar a imagem em {img_path}")
        return

    height, width = img.shape
    step = width / 6
    cut_points = [int(round(i * step)) for i in range(7)]  # 7 pontos para 6 divisões

    os.makedirs(save_path, exist_ok=True)
    base_name, ext = os.path.splitext(filename)

    prev_end_x = 0  # Para controlar avanço mínimo entre cortes

    for i in range(6):
        # Garante que o próximo corte avance pelo menos 'min_advance' pixels
        base_start_x = max(prev_end_x + min_advance, cut_points[i])
        base_end_x = cut_points[i + 1]

        region = img[:, base_start_x:base_end_x]
        proj = np.sum(region, axis=0)

        region_width = base_end_x - base_start_x
        center_local = int(np.argmax(proj))

        # Limitar deslocamento do centro (máx 25% da largura da região)
        center_shift = center_local - region_width // 2
        max_shift = region_width // 4
        clamped_shift = int(np.clip(center_shift, -max_shift, max_shift))
        adjusted_center = base_start_x + region_width // 2 + clamped_shift

        # Define faixa de corte com margem
        start_x = int(max(0, adjusted_center - region_width // 2 - margin))
        end_x = int(min(width, adjusted_center + region_width // 2 + margin))

        # Impor limite máximo de largura
        if end_x - start_x > max_char_width:
            extra = (end_x - start_x - max_char_width) // 2
            start_x += extra
            end_x -= extra

        # Atualiza o fim da faixa atual para o controle do próximo corte
        prev_end_x = end_x

        char_img = img[:, start_x:end_x]

        # Salvar
        char_filename = f"{base_name}_{i}{ext}"
        save_path_full = os.path.join(save_path, char_filename)
        cv2.imwrite(save_path_full, char_img)
        print(f"Salvo: {save_path_full}")

        # Debug visual
        if debug:
            img_debug = cv2.cvtColor(img, cv2.COLOR_GRAY2BGR)
            cv2.rectangle(img_debug, (start_x, 0), (end_x, height), (0, 255, 0), 2)
            cv2.imshow(f"Char {i}", img_debug)
            cv2.waitKey(0)

    if debug:
        cv2.destroyAllWindows()

In [13]:
conjuntos = ['treinamento', 'teste', 'validacao']
clean_base_path = '/home/bernardo/TP2-ICV/dados/processed'
for conjunto in conjuntos:
    folder_clean = os.path.join(conjunto, 'cleanImage')
    full_clean_folder = os.path.join(clean_base_path, folder_clean)

    for filename in tqdm(os.listdir(full_clean_folder), desc=f"Segmentando {conjunto}"):
        if filename.endswith('.jpg'):
            save_folder = os.path.join(clean_base_path, conjunto)

            split_image(
                path=clean_base_path,
                folder=folder_clean,        
                filename=filename,
                save_path=save_folder,      
                debug=False
            )


Segmentando treinamento:   1%|          | 63/8000 [00:00<00:12, 623.60it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/000018_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/003567_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treina

Segmentando treinamento:   4%|▍         | 305/8000 [00:00<00:09, 779.41it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005047_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002461_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/treina

Segmentando treinamento:   5%|▍         | 383/8000 [00:00<00:09, 765.19it/s]

...

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008129_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008205_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008042_cleaned_0.jpg

Segmentando validacao:  94%|█████████▍| 938/1000 [00:01<00:00, 606.28it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008120_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008120_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008702_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008187_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008187_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008187_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008187_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008187_cleaned_4.jpg

Segmentando validacao: 100%|██████████| 1000/1000 [00:01<00:00, 642.34it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008468_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_0.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_1.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_2.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_3.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_4.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008714_cleaned_5.jpg
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008262_cleaned_0.jpg